# Entrenamiento de una Red neuronal Pequeña.
Código Basado en https://machinelearningmastery.com/implement-backpropagation-algorithm-scratch-python/

In [21]:
from math import exp
from random import seed, random
import math

* Una red neuronal es una función universal con  3 tipos de capas: capa de entrada, capas intermedia capa de salida. 

* Un problema es que la derivada no se puede calcular directamente. A partir de la capa de salida, no se tiene acceso a las derivadas de las capas intermedias.

* Por lo tanto se requiere un algoritmo especial para calcular la derivada basada en la regla de la cadena de cálculo que indica que si se tienen funciones anidadas: $y=g(x), z = f(y)$ o bien $z = f(g(x))$, una manera de resolver esta anidación es aplicando la regla de la cadena. Ejemplo:

$$\frac{d z}{d x} = \frac{dz}{dy} \frac{dy}{dy} $$

* El algoritmo de **Propagación hacia atrás** (Backpropagation, BP), es un algoritmo de entrenamiento supervisado permite calcular la derivada de una red neuronal y por lo tanto actualizar los pesos de todas las capas intermedias.

* Por lo tanto describiremos un código de una red neuronal con fines didácticos. 




Ejemplo Red neuronal multicapa

**Inicializando la red**

initialize_network recibe el tamaño del vector de entrada, el número de capas ocultas y el numero de capas de salida.

Si inicializamos initialize_network(3, 2, 2), tendremos 2 conjuntos de 3+1 pesos considerando el *bias* para la primera capa que asocia cada entrada de $[x_0,x_1,x_0]$ con cada neurona intermedia. 


In [22]:

def initialize_network(n_inputs, n_hidden, n_outputs):
    network = list()
    hidden_layer = [{'weights':[random() for i in range(n_inputs + 1)]} for i in range(n_hidden)]
    network.append(hidden_layer)
    output_layer = [{'weights':[random() for i in range(n_hidden + 1)]} for i in range(n_outputs)]
    network.append(output_layer)
    return network

seed(1)
network = initialize_network(3, 2, 2)

print("capa de entrada:", network[0])
print("capa de salida:", network[1])

capa de entrada: [{'weights': [0.13436424411240122, 0.8474337369372327, 0.763774618976614, 0.2550690257394217]}, {'weights': [0.49543508709194095, 0.4494910647887381, 0.651592972722763, 0.7887233511355132]}]
capa de salida: [{'weights': [0.0938595867742349, 0.02834747652200631, 0.8357651039198697]}, {'weights': [0.43276706790505337, 0.762280082457942, 0.0021060533511106927]}]


**Propagación hacia adelante** (Forwad propagation): salida de la red neuronal dada una entrada $\mathbf{x}$

Es la función que nos permite utilizar la red neuronal para hacer clasificación. La entrada se va procesando a través de las capas hasta obtener una salida.

**Activación de la neurona**

Es el cálculo de una regresión lineal de la forma 

$$y = \mathbf{x}\mathbf{w}^T + w_0 $$

In [23]:
# Calculate neuron activation for an input
def activate(weights, inputs):
    # W*X+w_0
    
    #bias: w_0
    activation = weights[-1]
    
    #calcular w_0 + W*X
    for i in range(len(weights)-1):
        activation += weights[i] * inputs[i]
        
    return activation

**Transferencia de la neurona**

Existen muchas funciones de transferencia como relu, tanh identidad, pero una de las mas utilizadas es la función sigmoide con forma de s o también llamada curva logística. Tiene la forma:

$$x = 1/(1+e^{-y}))$$

In [24]:
# Transfer neuron activation
def transfer(activation):
    return 1.0 / (1.0 + exp(-activation))
 

**Propagación hacia adelante**

Es la red neuronal en funcionamiento. Recibe una entrada $\mathbf{x_i}$ y regresa una salida $y_i$

In [25]:
# Forward propagate input to a network output
def forward_propagate(network, row):
    inputs = row
    for layer in network:
        new_inputs = []
        for neuron in layer:
            activation = activate(neuron['weights'], inputs)
            neuron['output'] = transfer(activation)
            new_inputs.append(neuron['output'])
        inputs = new_inputs
    return inputs

In [26]:
# Inventamos una red neuronal con la representación descrita
network = [[{'weights': [0.13436424411240122, 0.8474337369372327, 0.763774618976614]}],
[{'weights': [0.2550690257394217, 0.49543508709194095]}, {'weights': [0.4494910647887381, 0.651592972722763]}]]

#utilizamos un vector de entrada innventado
row = [10, 20]

#esta es la red en funcionamiento
output = forward_propagate(network, row)
print(output)

[0.679288532620084, 0.7504631660186395]


**Derivada de transferencia hacia atrás de las capas intermedias**

Esta derivada es solo una parte de la derivda de toda la red neuronal que se hace en forma encadenada. 

In [27]:
# Esta es la derivada de la función sigmoide
def transfer_derivative(output):
    return output * (1.0 - output)

**Propagación hacia atrás del error**

In [28]:

 
# Propaga el error hacia atrás y lo va guardando en la estructura de la red
def backward_propagate_error(network, expected):
    
    #comenzamos con la capa de salida
    for i in reversed(range(len(network))):
        
        # por cada capa de la red asignada a layer
        layer = network[i]
        
        #el tamaño de la capa es equivalente al numero de neuronas en la capa
        n_neuronas = len(layer)
        
        #inicializamos error
        errors = list()
        
        # la primera vez calculamos sobre la ultima capa que es a la que tenemos acceso en un inicio
        if i == len(network)-1:
            
            # por cada neurona de la capa hacer:
            for j in range(n_neuronas):
            
                neuron = layer[j]

                yhat = neuron['output']
                y = expected[j]
            
                #esta es la derivada de la función de costo basada en la log verosimilitud
                # LL(\theta) = (y log yhat + (1-y) log [1-yhat])
                # Aqui comienza la transferencia
                e = (yhat-y)/((yhat-1)*yhat)
                errors.append(e)
        
        else:
            #aqui son las capas restantes hacia atrás donde propagamos el erro
            
            for j in range(n_neuronas):
                error = 0.0
                for neuron in network[i + 1]:
                    error += (neuron['weights'][j] * neuron['delta'])
                errors.append(error)
                
        #aqui guardamos todos los delta asociada a cada neurona de cada capa
        for j in range(n_neuronas):
            neuron = layer[j]
            
            #el error magnifica el delta que depende de derivada de transferencia
            neuron['delta'] = errors[j] * transfer_derivative(neuron['output'])
 

**Actualizar pesos con el error**

Se recibe la red con los deltas, y un vector de entrada $row$ y la tasa de aprendizaje $l_rate$ asignada por el usuario la cual especifica en porcentaje de actualización que queremos para los pesos.

In [33]:
# Update network weights with error
def update_weights(network, row, l_rate):
    
    # por cada capa de la red
    for i in range(len(network)):
        
        #extraer la clasificación real del vector de entrada. 
        inputs = row[:-1]
        
        #las salidas ahora son las entradas de la siguiente capa
        if i != 0:
            inputs = [neuron['output'] for neuron in network[i - 1]]
 
        for neuron in network[i]:
            for j in range(len(inputs)):
                
                # por cada neurona y cada una de sus entradas
                neuron['weights'][j] += l_rate * neuron['delta'] * inputs[j]
            
            #actualización del bias
            neuron['weights'][-1] += l_rate * neuron['delta']
           

       
 

**Entrenar la red con Gradiente Descendiente estocástico**

* una característica diferente a Gradiente descendiente normal, es que por cada iteación, utiliza un vector de entrada diferente para actualizar los pesos.

In [34]:


def train_network(network, train, l_rate, n_epoch, n_outputs):
    for epoch in range(n_epoch):
        sum_error = 0
        
        #por cada vector en el conjunto de entrenamiento.
        for row in train:
            
            # se calcular la salida de un elemento del vector
            outputs = forward_propagate(network, row)
            
            #preparamos con ceros
            expected = [0 for i in range(n_outputs)]
            
            #la posición row[-1] \in {0,1} tendrá un 1
            expected[int(row[-1])] = 1
            
            #sumamos cada error en cada dimensión diferente
            
            #sum_error += sum([(expected[i]-outputs[i] )**2 for i in range(len(expected))])
            
            zi = expected[1]
            zi_e = outputs[1]
            
            #aquí el error reportado es la suma log verosimilitud , queremos que sea el máximo
            sum_error += zi*math.log(zi_e)+(1-zi)*math.log(1-zi_e)
        
            #print(expected)
            #propagamos hacia atrás 
            #el error generado por la diferencia de el valor esperado y el valor generado por la red
            # se reajusta la red para predecir mejor el valor esperado
            backward_propagate_error(network, expected)
            update_weights(network, row, l_rate)
        print('>epoch=%d, lrate=%.3f, error=%.3f' % (epoch, l_rate, sum_error))
 



In [53]:
seed(1)


dataset = [[ 0.        , 43.57879291,  0.        ],
       [ 1.        , 38.25686159,  0.        ],
       [ 2.        , 33.65222425,  0.        ],
       [ 3.        , 35.58326609,  0.        ],
       [ 4.        , 34.71588722,  0.        ],
       [ 5.        , 32.38702072,  0.        ],
       [ 6.        , 28.39419039,  0.        ],
       [ 7.        , 20.20082333,  0.        ],
       [ 8.        , 24.19586975,  0.        ],
       [ 9.        , 18.48536939,  0.        ],
       [10.        , 19.43098795,  0.        ],
       [11.        ,  9.78931084,  0.        ],
       [12.        , 14.4403072 ,  0.        ],
       [13.        ,  8.95888303,  0.        ],
       [14.        ,  7.17704765,  0.        ],
       [15.        ,  9.57779397,  0.        ],
       [16.        ,  7.58424501,  0.        ],
       [17.        ,  8.9341588 ,  0.        ],
       [18.        ,  3.13378008,  0.        ],
       [19.        ,  9.23532406,  0.        ],
       [20.        ,  6.43370902,  0.        ],
       [21.        ,  6.67961846,  0.        ],
       [22.        ,  5.15107388,  0.        ],
       [23.        ,  3.13252828,  0.        ],
       [24.        ,  9.40036651,  0.        ],
       [25.        ,  8.96646931,  0.        ],
       [26.        , 12.97187713,  0.        ],
       [27.        ,  6.17097537,  0.        ],
       [28.        , 14.94380716,  0.        ],
       [29.        , 15.78038035,  0.        ],
       [30.        , 13.44006058,  0.        ],
       [31.        , 12.38640541,  0.        ],
       [32.        , 18.24681531,  0.        ],
       [33.        , 24.89568658,  0.        ],
       [34.        , 20.9740082 ,  0.        ],
       [35.        , 29.60592301,  0.        ],
       [36.        , 28.15828701,  0.        ],
       [37.        , 36.2793585 ,  0.        ],
       [38.        , 35.14373666,  0.        ],
       [39.        , 45.91909167,  0.        ],
       [ 0.        , 72.99963497,  1.        ],
       [ 1.        , 66.25249531,  1.        ],
       [ 2.        , 69.47862325,  1.        ],
       [ 3.        , 68.12423544,  1.        ],
       [ 4.        , 58.18406218,  1.        ],
       [ 5.        , 59.71572434,  1.        ],
       [ 6.        , 56.45457802,  1.        ],
       [ 7.        , 52.4068255 ,  1.        ],
       [ 8.        , 47.24274882,  1.        ],
       [ 9.        , 43.36311311,  1.        ],
       [10.        , 44.07483255,  1.        ],
       [11.        , 39.85302512,  1.        ],
       [12.        , 44.01192218,  1.        ],
       [13.        , 41.07318483,  1.        ],
       [14.        , 33.8127034 ,  1.        ],
       [15.        , 33.21045858,  1.        ],
       [16.        , 37.15741812,  1.        ],
       [17.        , 31.73730861,  1.        ],
       [18.        , 34.83305033,  1.        ],
       [19.        , 39.87419754,  1.        ],
       [20.        , 31.48844934,  1.        ],
       [21.        , 35.0882841 ,  1.        ],
       [22.        , 39.71262275,  1.        ],
       [23.        , 31.62777132,  1.        ],
       [24.        , 40.68066481,  1.        ],
       [25.        , 36.14619892,  1.        ],
       [26.        , 38.39007043,  1.        ],
       [27.        , 35.30625817,  1.        ],
       [28.        , 38.9855814 ,  1.        ],
       [29.        , 44.46375169,  1.        ],
       [30.        , 42.9567545 ,  1.        ],
       [31.        , 43.13876601,  1.        ],
       [32.        , 46.36785753,  1.        ],
       [33.        , 53.20209487,  1.        ],
       [34.        , 54.57671019,  1.        ],
       [35.        , 61.72180758,  1.        ],
       [36.        , 56.20328364,  1.        ],
       [37.        , 60.75140654,  1.        ],
       [38.        , 62.61155513,  1.        ],
       [39.        , 67.27858905,  1.        ]]



n_inputs = len(dataset[0]) - 1
print("inputs: ", n_inputs)

#total possible number of output values
n_outputs = len(set([ int(row[-1]) for row in dataset]))
print("outputs: ", n_outputs)

network = initialize_network(n_inputs, 4, n_outputs)
train_network(network, dataset, 0.01, 100000, n_outputs)
for layer in network:
    print(layer)

inputs:  2
outputs:  2
>epoch=0, lrate=0.010, error=-84.044
>epoch=1, lrate=0.010, error=-63.261
>epoch=2, lrate=0.010, error=-57.540
>epoch=3, lrate=0.010, error=-55.940
>epoch=4, lrate=0.010, error=-55.428
>epoch=5, lrate=0.010, error=-55.249
>epoch=6, lrate=0.010, error=-55.184
>epoch=7, lrate=0.010, error=-55.159
>epoch=8, lrate=0.010, error=-55.150
>epoch=9, lrate=0.010, error=-55.146
>epoch=10, lrate=0.010, error=-55.144
>epoch=11, lrate=0.010, error=-55.144
>epoch=12, lrate=0.010, error=-55.143
>epoch=13, lrate=0.010, error=-55.143
>epoch=14, lrate=0.010, error=-55.142
>epoch=15, lrate=0.010, error=-55.142
>epoch=16, lrate=0.010, error=-55.142
>epoch=17, lrate=0.010, error=-55.142
>epoch=18, lrate=0.010, error=-55.142
>epoch=19, lrate=0.010, error=-55.141
>epoch=20, lrate=0.010, error=-55.141
>epoch=21, lrate=0.010, error=-55.141
>epoch=22, lrate=0.010, error=-55.141
>epoch=23, lrate=0.010, error=-55.141
>epoch=24, lrate=0.010, error=-55.141
>epoch=25, lrate=0.010, error=-55.140

>epoch=218, lrate=0.010, error=-32.773
>epoch=219, lrate=0.010, error=-32.658
>epoch=220, lrate=0.010, error=-32.547
>epoch=221, lrate=0.010, error=-32.439
>epoch=222, lrate=0.010, error=-32.335
>epoch=223, lrate=0.010, error=-32.235
>epoch=224, lrate=0.010, error=-32.138
>epoch=225, lrate=0.010, error=-32.045
>epoch=226, lrate=0.010, error=-31.955
>epoch=227, lrate=0.010, error=-31.867
>epoch=228, lrate=0.010, error=-31.783
>epoch=229, lrate=0.010, error=-31.702
>epoch=230, lrate=0.010, error=-31.623
>epoch=231, lrate=0.010, error=-31.547
>epoch=232, lrate=0.010, error=-31.473
>epoch=233, lrate=0.010, error=-31.402
>epoch=234, lrate=0.010, error=-31.333
>epoch=235, lrate=0.010, error=-31.266
>epoch=236, lrate=0.010, error=-31.201
>epoch=237, lrate=0.010, error=-31.139
>epoch=238, lrate=0.010, error=-31.078
>epoch=239, lrate=0.010, error=-31.019
>epoch=240, lrate=0.010, error=-30.962
>epoch=241, lrate=0.010, error=-30.906
>epoch=242, lrate=0.010, error=-30.852
>epoch=243, lrate=0.010, 

>epoch=451, lrate=0.010, error=-27.484
>epoch=452, lrate=0.010, error=-27.481
>epoch=453, lrate=0.010, error=-27.478
>epoch=454, lrate=0.010, error=-27.474
>epoch=455, lrate=0.010, error=-27.471
>epoch=456, lrate=0.010, error=-27.468
>epoch=457, lrate=0.010, error=-27.465
>epoch=458, lrate=0.010, error=-27.462
>epoch=459, lrate=0.010, error=-27.458
>epoch=460, lrate=0.010, error=-27.455
>epoch=461, lrate=0.010, error=-27.452
>epoch=462, lrate=0.010, error=-27.449
>epoch=463, lrate=0.010, error=-27.446
>epoch=464, lrate=0.010, error=-27.443
>epoch=465, lrate=0.010, error=-27.440
>epoch=466, lrate=0.010, error=-27.437
>epoch=467, lrate=0.010, error=-27.434
>epoch=468, lrate=0.010, error=-27.431
>epoch=469, lrate=0.010, error=-27.429
>epoch=470, lrate=0.010, error=-27.426
>epoch=471, lrate=0.010, error=-27.423
>epoch=472, lrate=0.010, error=-27.420
>epoch=473, lrate=0.010, error=-27.417
>epoch=474, lrate=0.010, error=-27.415
>epoch=475, lrate=0.010, error=-27.412
>epoch=476, lrate=0.010, 

>epoch=704, lrate=0.010, error=-27.092
>epoch=705, lrate=0.010, error=-27.092
>epoch=706, lrate=0.010, error=-27.091
>epoch=707, lrate=0.010, error=-27.090
>epoch=708, lrate=0.010, error=-27.089
>epoch=709, lrate=0.010, error=-27.089
>epoch=710, lrate=0.010, error=-27.088
>epoch=711, lrate=0.010, error=-27.087
>epoch=712, lrate=0.010, error=-27.087
>epoch=713, lrate=0.010, error=-27.086
>epoch=714, lrate=0.010, error=-27.085
>epoch=715, lrate=0.010, error=-27.085
>epoch=716, lrate=0.010, error=-27.084
>epoch=717, lrate=0.010, error=-27.083
>epoch=718, lrate=0.010, error=-27.082
>epoch=719, lrate=0.010, error=-27.082
>epoch=720, lrate=0.010, error=-27.081
>epoch=721, lrate=0.010, error=-27.080
>epoch=722, lrate=0.010, error=-27.080
>epoch=723, lrate=0.010, error=-27.079
>epoch=724, lrate=0.010, error=-27.078
>epoch=725, lrate=0.010, error=-27.078
>epoch=726, lrate=0.010, error=-27.077
>epoch=727, lrate=0.010, error=-27.076
>epoch=728, lrate=0.010, error=-27.076
>epoch=729, lrate=0.010, 

>epoch=964, lrate=0.010, error=-26.969
>epoch=965, lrate=0.010, error=-26.969
>epoch=966, lrate=0.010, error=-26.969
>epoch=967, lrate=0.010, error=-26.968
>epoch=968, lrate=0.010, error=-26.968
>epoch=969, lrate=0.010, error=-26.968
>epoch=970, lrate=0.010, error=-26.967
>epoch=971, lrate=0.010, error=-26.967
>epoch=972, lrate=0.010, error=-26.967
>epoch=973, lrate=0.010, error=-26.966
>epoch=974, lrate=0.010, error=-26.966
>epoch=975, lrate=0.010, error=-26.966
>epoch=976, lrate=0.010, error=-26.965
>epoch=977, lrate=0.010, error=-26.965
>epoch=978, lrate=0.010, error=-26.965
>epoch=979, lrate=0.010, error=-26.965
>epoch=980, lrate=0.010, error=-26.964
>epoch=981, lrate=0.010, error=-26.964
>epoch=982, lrate=0.010, error=-26.964
>epoch=983, lrate=0.010, error=-26.963
>epoch=984, lrate=0.010, error=-26.963
>epoch=985, lrate=0.010, error=-26.963
>epoch=986, lrate=0.010, error=-26.963
>epoch=987, lrate=0.010, error=-26.962
>epoch=988, lrate=0.010, error=-26.962
>epoch=989, lrate=0.010, 

...

>epoch=98988, lrate=0.010, error=-26.742
>epoch=98989, lrate=0.010, error=-26.742
>epoch=98990, lrate=0.010, error=-26.742
>epoch=98991, lrate=0.010, error=-26.742
>epoch=98992, lrate=0.010, error=-26.742
>epoch=98993, lrate=0.010, error=-26.742
>epoch=98994, lrate=0.010, error=-26.742
>epoch=98995, lrate=0.010, error=-26.742
>epoch=98996, lrate=0.010, error=-26.742
>epoch=98997, lrate=0.010, error=-26.742
>epoch=98998, lrate=0.010, error=-26.742
>epoch=98999, lrate=0.010, error=-26.742
>epoch=99000, lrate=0.010, error=-26.742
>epoch=99001, lrate=0.010, error=-26.742
>epoch=99002, lrate=0.010, error=-26.742
>epoch=99003, lrate=0.010, error=-26.742
>epoch=99004, lrate=0.010, error=-26.742
>epoch=99005, lrate=0.010, error=-26.742
>epoch=99006, lrate=0.010, error=-26.742
>epoch=99007, lrate=0.010, error=-26.742
>epoch=99008, lrate=0.010, error=-26.742
>epoch=99009, lrate=0.010, error=-26.742
>epoch=99010, lrate=0.010, error=-26.742
>epoch=99011, lrate=0.010, error=-26.742
>epoch=99012, lr

>epoch=99234, lrate=0.010, error=-26.742
>epoch=99235, lrate=0.010, error=-26.742
>epoch=99236, lrate=0.010, error=-26.742
>epoch=99237, lrate=0.010, error=-26.742
>epoch=99238, lrate=0.010, error=-26.742
>epoch=99239, lrate=0.010, error=-26.742
>epoch=99240, lrate=0.010, error=-26.742
>epoch=99241, lrate=0.010, error=-26.742
>epoch=99242, lrate=0.010, error=-26.742
>epoch=99243, lrate=0.010, error=-26.742
>epoch=99244, lrate=0.010, error=-26.742
>epoch=99245, lrate=0.010, error=-26.742
>epoch=99246, lrate=0.010, error=-26.742
>epoch=99247, lrate=0.010, error=-26.742
>epoch=99248, lrate=0.010, error=-26.742
>epoch=99249, lrate=0.010, error=-26.742
>epoch=99250, lrate=0.010, error=-26.742
>epoch=99251, lrate=0.010, error=-26.742
>epoch=99252, lrate=0.010, error=-26.742
>epoch=99253, lrate=0.010, error=-26.742
>epoch=99254, lrate=0.010, error=-26.742
>epoch=99255, lrate=0.010, error=-26.742
>epoch=99256, lrate=0.010, error=-26.742
>epoch=99257, lrate=0.010, error=-26.742
>epoch=99258, lr

>epoch=99483, lrate=0.010, error=-26.742
>epoch=99484, lrate=0.010, error=-26.742
>epoch=99485, lrate=0.010, error=-26.742
>epoch=99486, lrate=0.010, error=-26.742
>epoch=99487, lrate=0.010, error=-26.742
>epoch=99488, lrate=0.010, error=-26.742
>epoch=99489, lrate=0.010, error=-26.742
>epoch=99490, lrate=0.010, error=-26.742
>epoch=99491, lrate=0.010, error=-26.742
>epoch=99492, lrate=0.010, error=-26.742
>epoch=99493, lrate=0.010, error=-26.742
>epoch=99494, lrate=0.010, error=-26.742
>epoch=99495, lrate=0.010, error=-26.742
>epoch=99496, lrate=0.010, error=-26.742
>epoch=99497, lrate=0.010, error=-26.742
>epoch=99498, lrate=0.010, error=-26.742
>epoch=99499, lrate=0.010, error=-26.742
>epoch=99500, lrate=0.010, error=-26.742
>epoch=99501, lrate=0.010, error=-26.742
>epoch=99502, lrate=0.010, error=-26.742
>epoch=99503, lrate=0.010, error=-26.742
>epoch=99504, lrate=0.010, error=-26.742
>epoch=99505, lrate=0.010, error=-26.742
>epoch=99506, lrate=0.010, error=-26.742
>epoch=99507, lr

>epoch=99735, lrate=0.010, error=-26.742
>epoch=99736, lrate=0.010, error=-26.742
>epoch=99737, lrate=0.010, error=-26.742
>epoch=99738, lrate=0.010, error=-26.742
>epoch=99739, lrate=0.010, error=-26.742
>epoch=99740, lrate=0.010, error=-26.742
>epoch=99741, lrate=0.010, error=-26.742
>epoch=99742, lrate=0.010, error=-26.742
>epoch=99743, lrate=0.010, error=-26.742
>epoch=99744, lrate=0.010, error=-26.742
>epoch=99745, lrate=0.010, error=-26.742
>epoch=99746, lrate=0.010, error=-26.742
>epoch=99747, lrate=0.010, error=-26.742
>epoch=99748, lrate=0.010, error=-26.742
>epoch=99749, lrate=0.010, error=-26.742
>epoch=99750, lrate=0.010, error=-26.742
>epoch=99751, lrate=0.010, error=-26.742
>epoch=99752, lrate=0.010, error=-26.742
>epoch=99753, lrate=0.010, error=-26.742
>epoch=99754, lrate=0.010, error=-26.742
>epoch=99755, lrate=0.010, error=-26.742
>epoch=99756, lrate=0.010, error=-26.742
>epoch=99757, lrate=0.010, error=-26.742
>epoch=99758, lrate=0.010, error=-26.742
>epoch=99759, lr

>epoch=99992, lrate=0.010, error=-26.742
>epoch=99993, lrate=0.010, error=-26.742
>epoch=99994, lrate=0.010, error=-26.742
>epoch=99995, lrate=0.010, error=-26.742
>epoch=99996, lrate=0.010, error=-26.742
>epoch=99997, lrate=0.010, error=-26.742
>epoch=99998, lrate=0.010, error=-26.742
>epoch=99999, lrate=0.010, error=-26.742
[{'weights': [0.18424527965839116, 0.8582515585588678, 0.7663579622045898], 'output': 1.0, 'delta': -0.0}, {'weights': [-4.5253813549271324, 3.804089671319545, -2.3703195726623103], 'output': 1.0, 'delta': 0.0}, {'weights': [0.6517128007511684, 0.7889294998078071, 0.09387194892602108], 'output': 1.0, 'delta': -0.0}, {'weights': [0.22042822802483925, 0.8737059810846695, 0.44256339771712067], 'output': 1.0, 'delta': -0.0}]
[{'weights': [2.672365673984936, -11.312517942697355, 2.3627248861630044, 2.628820856537145, 2.1461041437771904], 'output': 0.18342224844157387, 'delta': -0.18342224844157387}, {'weights': [-1.8901205360903912, 11.312466779297406, -2.8121279106300

In [56]:
e = 0
for x in dataset:
    
    y = forward_propagate(network, x[:2])
    print("expectation:",x[-1],"reality",1*((y[-1])>0.5))
    
    e+= (x[-1]- 1*((y[-1])>0.5))**2
    


expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 1
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
expectation: 0.0 reality 0
e

In [57]:
e

11.0

In [40]:
import matplotlib.pyplot as plt



In [52]:
import numpy as np
ds = np.array(dataset)

plt.scatter(ds[:40,0],ds[:40,1])
plt.scatter(ds[40:,0],ds[40:,1])

In [7]:

import matplotlib.pyplot as plt

In [59]:
len(dataset[0]) - 1

#plt.scatter(dsnp[:5,0],dsnp[:5,1])
#plt.scatter(dsnp[5:,0],dsnp[5:,1])

2

In [44]:
a = 10

x = np.arange(0,20)
y = a*(x-10)**2

#Agregamos ruido uniformemente distribuido 

y_noise_00 = y +np.random.rand(len(x))*300-50

y_noise_01 = y +np.random.rand(len(x))*300-50+400

plt.scatter(x,y_noise_00)

plt.scatter(x,y_noise_01)

In [46]:
class_00 = np.append([x],[y_noise_00],axis=0).T
zeros = np.zeros(len(class_00)).T

labeled_class00 = np.append(class_00,np.transpose([zeros]),axis=1)
labeled_class00

class_01 = np.append([x],[y_noise_01],axis=0).T


ones = np.ones(len(class_01)).T

labeled_class01 = np.append(class_01,np.transpose([ones]),axis=1)

ones = ones*0
labeled_class00 = np.append(class_00,np.transpose([ones]),axis=1)

In [49]:
labeled_class00

array([[0.00000000e+00, 1.01388977e+03, 0.00000000e+00],
       [1.00000000e+00, 8.60935995e+02, 0.00000000e+00],
       [2.00000000e+00, 7.03252487e+02, 0.00000000e+00],
       [3.00000000e+00, 6.44233555e+02, 0.00000000e+00],
       [4.00000000e+00, 3.62598438e+02, 0.00000000e+00],
       [5.00000000e+00, 4.09206887e+02, 0.00000000e+00],
       [6.00000000e+00, 3.94882732e+02, 0.00000000e+00],
       [7.00000000e+00, 5.39039326e+01, 0.00000000e+00],
       [8.00000000e+00, 1.98724598e+02, 0.00000000e+00],
       [9.00000000e+00, 1.71607402e+02, 0.00000000e+00],
       [1.00000000e+01, 1.81752375e+02, 0.00000000e+00],
       [1.10000000e+01, 1.90391042e+02, 0.00000000e+00],
       [1.20000000e+01, 2.24171165e+02, 0.00000000e+00],
       [1.30000000e+01, 8.97044143e+01, 0.00000000e+00],
       [1.40000000e+01, 3.47558908e+02, 0.00000000e+00],
       [1.50000000e+01, 3.49409536e+02, 0.00000000e+00],
       [1.60000000e+01, 3.53624334e+02, 0.00000000e+00],
       [1.70000000e+01, 5.22692

In [94]:
len(labeled_class01)

20

In [ ]:



dataset = [[0.00000000e+00, 1.01388977e+03, 0],
       [1.00000000e+00, 8.60935995e+02, 0],
       [2.00000000e+00, 7.03252487e+02, 0],
       [3.00000000e+00, 6.44233555e+02, 0],
       [4.00000000e+00, 3.62598438e+02, 0],
       [5.00000000e+00, 4.09206887e+02, 0],
       [6.00000000e+00, 3.94882732e+02, 0],
       [7.00000000e+00, 5.39039326e+01, 0],
       [8.00000000e+00, 1.98724598e+02, 0],
       [9.00000000e+00, 1.71607402e+02, 0],
       [1.00000000e+01, 1.81752375e+02, 0],
       [1.10000000e+01, 1.90391042e+02, 0],
       [1.20000000e+01, 2.24171165e+02, 0],
       [1.30000000e+01, 8.97044143e+01, 0],
       [1.40000000e+01, 3.47558908e+02, 0],
       [1.50000000e+01, 3.49409536e+02, 0],
       [1.60000000e+01, 3.53624334e+02, 0],
       [1.70000000e+01, 5.22692351e+02, 0],
       [1.80000000e+01, 6.10003976e+02, 0],
       [1.90000000e+01, 9.16947322e+02, 0],
       [0.00000000e+00, 1.38446715e+03, 1],
       [1.00000000e+00, 1.30679087e+03, 1],
       [2.00000000e+00, 1.25575128e+03, 1],
       [3.00000000e+00, 1.12472540e+03, 1],
       [4.00000000e+00, 7.46112751e+02, 1],
       [5.00000000e+00, 6.08208439e+02, 1],
       [6.00000000e+00, 7.31643422e+02, 1],
       [7.00000000e+00, 4.78377651e+02, 1],
       [8.00000000e+00, 6.40309421e+02, 1],
       [9.00000000e+00, 3.85883000e+02, 1],
       [1.00000000e+01, 4.76000525e+02, 1],
       [1.10000000e+01, 3.78412573e+02, 1],
       [1.20000000e+01, 5.03105104e+02, 1],
       [1.30000000e+01, 6.38630629e+02, 1],
       [1.40000000e+01, 5.22602375e+02, 1],
       [1.50000000e+01, 8.90526756e+02, 1],
       [1.60000000e+01, 8.95002547e+02, 1],
       [1.70000000e+01, 1.12663046e+03, 1],
       [1.80000000e+01, 1.01774841e+03, 1],
       [1.90000000e+01, 1.18196703e+03, 1]]